# Hyperopt

Оптимизация параметров алгоритма на данных первого года

In [533]:
import hyperopt as hp
from hyperopt import fmin, tpe, hp, STATUS_OK, Trials

In [609]:
with pd.option_context('display.max_columns', None):
    display(X.iloc[:8808])

product_1_plan  product_1_plan_cumsum  product_1_fact  \
0              800.0                 4700.0         836.252   
1              800.0                 4700.0         836.252   
2              800.0                 4700.0         836.252   
3              800.0                 4700.0         836.252   
4              800.0                 4700.0         836.252   
...              ...                    ...             ...   
8803           700.0                 1300.0         204.774   
8804           700.0                 1300.0         204.774   
8805           700.0                 1300.0         204.774   
8806           700.0                 1300.0         204.774   
8807           700.0                 1300.0         204.774   

      product_1_fact_cumsum  product_2_plan  product_2_plan_cumsum  \
0                  3639.243           950.0                 3900.0   
1                  3639.243           950.0                 3900.0   
2                  3639.243           950.0                 3900.0   
3                  3639.243           950.0                 3900.0   
4                  3639.243           950.0                 3900.0   
...                     ...             ...                    ...   
8803                925.929           750.0                12540.0   
8804                925.929           750.0                12540.0   
8805                925.929           750.0                12540.0   
8806                925.929           750.0                12540.0   
8807                925.929           750.0                12540.0   

      product_2_fact  product_2_fact_cumsum  product_2_accomplished  \
0            969.786               3502.537              118.730068   
1            969.786               3502.537              118.730068   
2            969.786               3502.537              118.730068   
3            969.786               3502.537              118.730068   
4            969.786               3502.537              118.730068   
...              ...                    ...                     ...   
8803           0.000                999.396              100.217049   
8804           0.000                999.396              100.217049   
8805           0.000                999.396              100.217049   
8806           0.000                999.396              100.217049   
8807           0.000                999.396              100.217049   

      product_3_plan  product_3_plan_cumsum  product_3_fact  \
0               25.0                  125.0          33.785   
1               25.0                  125.0          33.785   
2               25.0                  125.0          33.785   
3               25.0                  125.0          33.785   
4               25.0                  125.0          33.785   
...              ...                    ...             ...   
8803             4.0                  650.0           0.000   
8804             4.0                  650.0           0.000   
8805             4.0                  650.0           0.000   
8806             4.0                  650.0           0.000   
8807             4.0                  650.0           0.000   

      product_3_fact_cumsum  product_3_accomplished  product_4_fact  \
0                   170.816              170.816000           8.008   
1                   170.816              170.816000           8.008   
2                   170.816              170.816000           8.008   
3                   170.816              170.816000           8.008   
4                   170.816              170.816000           8.008   
...                     ...                     ...             ...   
8803                102.569              101.660923           6.049   
8804                102.569              101.660923           6.049   
8805                102.569              101.660923           6.049   
8806                102.569              101.660923           6.049   
8807             

In [610]:
from sklearn.model_selection import TimeSeriesSplit

tscv = TimeSeriesSplit(max_train_size= 8760, n_splits=int(X.iloc[:8808].shape[0]/24-1))
print(tscv)

TimeSeriesSplit(max_train_size=8760, n_splits=366)


In [561]:
start_time = time.time()

grid_params= {
    'metric': 'MAE',
    'learning_rate': 0.01,
    'n_estimators': hp.choice('num_leaves', [500, 1000, 2000]),
    'max_depth': hp.choice('max_depth', [4, 5, 6, 7]),    
    'max_bin': hp.choice('max_bin', [15, 31, 63, 127, 255]),
    'lambda_l2': hp.choice('lambda_l2', [0, 1, 5, 9, 15, 25, 40]),
    'lambda_l1': hp.choice('lambda_l1', [0, 1, 5, 9, 15, 25])
}
  
    
def func(params):
        
    rg_lgbm = lgbm.LGBMRegressor(**params)  
    y_pred_test = []
 
    for train_index, test_index in tscv.split(X.iloc[:8808]):
        if len(train_index)>=48:
            X_train, X_test = X.iloc[train_index, :], X.iloc[test_index,:]
            y_train, y_test = Y.iloc[train_index], Y.iloc[test_index]        
            rg_lgbm.fit(X_train, y_train, 
                    eval_set=[(X_test,  y_test)],
                    eval_metric='MAE',
                    early_stopping_rounds=100,
                    verbose=-1)        
            y_pred_test += list(rg_lgbm.predict(X_test))    
         
    mae_metric = mean_absolute_error(Y.iloc[48:], y_pred_test)

    return {'loss': mae_metric, 'status': STATUS_OK, 'params': params}

trials = Trials()

best = fmin(func, space=grid_params, algo=tpe.suggest, max_evals=30, trials=trials)

print(time.time() - start_time)

************************************************                                                                       
1                                                                                                                      
{'lambda_l1': 1, 'lambda_l2': 25, 'learning_rate': 0.01, 'max_bin': 127, 'max_depth': 5, 'metric': 'MAE', 'n_estimators': 2000}
Training until validation scores don't improve for 100 rounds.                                                         
Did not meet early stopping. Best iteration is:                                                                        
[2000]	valid_0's l1: 0.349679
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[1]	valid_0's l1: 1.01621
Training until validation scores don't improve for 100 rounds.                                  

Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[488]	valid_0's l1: 0.315838
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[285]	valid_0's l1: 0.086534
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[404]	valid_0's l1: 0.336673
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                       

Early stopping, best iteration is:                                                                                     
[458]	valid_0's l1: 0.154683
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[964]	valid_0's l1: 0.963066
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[1046]	valid_0's l1: 0.132502
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[66]	valid_0's l1: 0.86957
Training until validation scores don't improv

Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[829]	valid_0's l1: 0.159291
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[439]	valid_0's l1: 0.921136
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[595]	valid_0's l1: 0.454569
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                       

Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[1241]	valid_0's l1: 0.104829
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[401]	valid_0's l1: 0.843458
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[14]	valid_0's l1: 0.714262
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                       

...

Early stopping, best iteration is:                                                                                     
[381]	valid_0's l1: 0.204168
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[608]	valid_0's l1: 0.143566
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[282]	valid_0's l1: 0.0572101
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[473]	valid_0's l1: 0.301863
Training until validation scores don't impr

Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[463]	valid_0's l1: 0.149553
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[222]	valid_0's l1: 0.039187
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[752]	valid_0's l1: 0.0987658
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                      

Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[729]	valid_0's l1: 0.201608
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[334]	valid_0's l1: 0.0361988
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[928]	valid_0's l1: 0.220914
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                      

Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[810]	valid_0's l1: 0.171269
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[535]	valid_0's l1: 0.149021
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[1194]	valid_0's l1: 0.359249
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                      

Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[441]	valid_0's l1: 0.0563539
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[618]	valid_0's l1: 0.153018
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                                                                     
[797]	valid_0's l1: 0.176793
Training until validation scores don't improve for 100 rounds.                                                         
Early stopping, best iteration is:                                      

In [577]:
trials.results

[{'loss': 0.23449076169212946,
  'status': 'ok',
  'params': {'lambda_l1': 1,
   'lambda_l2': 25,
   'learning_rate': 0.01,
   'max_bin': 127,
   'max_depth': 5,
   'metric': 'MAE',
   'n_estimators': 2000}},
 {'loss': 0.23699773183774833,
  'status': 'ok',
  'params': {'lambda_l1': 5,
   'lambda_l2': 5,
   'learning_rate': 0.01,
   'max_bin': 255,
   'max_depth': 7,
   'metric': 'MAE',
   'n_estimators': 1000}},
 {'loss': 0.23626141529958758,
  'status': 'ok',
  'params': {'lambda_l1': 0,
   'lambda_l2': 25,
   'learning_rate': 0.01,
   'max_bin': 15,
   'max_depth': 6,
   'metric': 'MAE',
   'n_estimators': 2000}},
 {'loss': 0.2377838661321288,
  'status': 'ok',
  'params': {'lambda_l1': 5,
   'lambda_l2': 0,
   'learning_rate': 0.01,
   'max_bin': 63,
   'max_depth': 4,
   'metric': 'MAE',
   'n_estimators': 2000}},
 {'loss': 0.2326786875362135,
  'status': 'ok',
  'params': {'lambda_l1': 1,
   'lambda_l2': 15,
   'learning_rate': 0.01,
   'max_bin': 63,
   'max_depth': 5,
   'metri

In [578]:
loss=[]
my_params=[]

for i in range(0, 30):
    loss.append(trials.results[i]['loss'])
    my_params.append(trials.results[i]['params'])

In [579]:
res_opt = pd.concat([pd.Series(loss), pd.Series(my_params)],axis=1)\
             .rename(columns={0:'loss',1:'params'})  

In [581]:
res_opt.sort_values(by='loss')

loss                                             params
29  0.227773  {'lambda_l1': 1, 'lambda_l2': 1, 'learning_rat...
26  0.227773  {'lambda_l1': 1, 'lambda_l2': 1, 'learning_rat...
24  0.227773  {'lambda_l1': 1, 'lambda_l2': 1, 'learning_rat...
23  0.227773  {'lambda_l1': 1, 'lambda_l2': 1, 'learning_rat...
22  0.227773  {'lambda_l1': 1, 'lambda_l2': 1, 'learning_rat...
28  0.227773  {'lambda_l1': 1, 'lambda_l2': 1, 'learning_rat...
15  0.230204  {'lambda_l1': 1, 'lambda_l2': 0, 'learning_rat...
5   0.231248  {'lambda_l1': 1, 'lambda_l2': 0, 'learning_rat...
20  0.232066  {'lambda_l1': 1, 'lambda_l2': 5, 'learning_rat...
4   0.232679  {'lambda_l1': 1, 'lambda_l2': 15, 'learning_ra...
6   0.232933  {'lambda_l1': 1, 'lambda_l2': 0, 'learning_rat...
14  0.233073  {'lambda_l1': 1, 'lambda_l2': 9, 'learning_rat...
12  0.233570  {'lambda_l1': 0, 'lambda_l2': 0, 'learning_rat...
0   0.234491  {'lambda_l1': 1, 'lambda_l2': 25, 'learning_ra...
2   0.236261  {'lambda_l1': 0, 'lambda_l2': 25, 'learning_ra...
1   0.236998  {'lambda_l1': 5, 'lambda_l2': 5, 'learning_rat...
3   0.237784  {'lambda_l1': 5, 'lambda_l2': 0, 'learning_rat...
8   0.238320  {'lambda_l1': 5, 'lambda_l2': 0, 'learning_rat...
7   0.242237  {'lambda_l1': 0, 'lambda_l2': 25, 'learning_ra...
13  0.245493  {'lambda_l1': 9, 'lambda_l2': 0, 'learning_rat...
25  0.245604  {'lambda_l1': 9, 'lambda_l2': 1, 'learning_rat...
21  0.250479  {'lambda_l1': 9, 'lambda_l2': 15, 'learning_ra...
19  0.253302  {'lambda_l1': 0, 'lambda_l2': 40, 'learning_ra...
9   0.259069  {'lambda_l1': 15, 'lambda_l2': 1, 'learning_ra...
18  0.260790  {'lambda_l1': 5, 'lambda_l2': 40, 'learning_ra...
11  0.272532  {'lambda_l1': 25, 'lambda_l2': 0, 'learning_ra...
16  0.273380  {'lambda_l1': 15, 'lambda_l2': 25, 'learning_r...
17  0.273674  {'lambda_l1': 25, 'lambda_l2': 9, 'learning_ra...
10  0.274670  {'lambda_l1': 15, 'lambda_l2': 40, 'learning_r...
27  0.274993  {'lambda_l1': 25, 'lambda_l2': 1, 'learning_ra...

In [584]:
trials.results[29]

{'loss': 0.22777286907236355,
 'status': 'ok',
 'params': {'lambda_l1': 1,
  'lambda_l2': 1,
  'learning_rate': 0.01,
  'max_bin': 255,
  'max_depth': 7,
  'metric': 'MAE',
  'n_estimators': 2000}}